In [2]:
#preprocessing libriaris
import nltk
nltk.download("stopwords")
#stopwords modules
from nltk.corpus import stopwords
from pymystem3 import Mystem
from string import punctuation

[nltk_data] Downloading package stopwords to /home/alex/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
#Create lemmatizer and stopwords list
mystem = Mystem() 
russian_stopwords = stopwords.words("russian")

#Preprocess function (stopwords, puncuation, etc)
def preprocess_text(text):
    tokens = mystem.lemmatize(text.lower())
    tokens = [token for token in tokens if token not in russian_stopwords\
              and token != " " \
              and token.strip() not in punctuation]
    
    text = " ".join(tokens)
    
    return text

#Examples    
preprocess_text("<|startoftext|>Выкинь все, что есть в твоих мыслях: грусть, пустоту, печаль. Помнишь, как ты подарил мне лето, в то время, как был февраль.<|endoftext|>")

'<| startoftext |> выкидывать твой мысль грусть пустота печаль помнить подарить лето время февраль <| endoftext |>\n'

In [4]:
import pandas as pd
import numpy as np
import io

qoute_path = '../parsing/data/cleaned_tagged.txt'

df = pd.read_csv(qoute_path, sep='<\d*>', engine ='python', names=['quotes']) #reading quotes to the dataframe
with open(qoute_path, 'r', encoding='utf-8') as file:
    data = file.read().replace('\n', ' nextquote ')
    processed_data = preprocess_text(data)  #preprocessing qoutes
#dataframe with quotes and their processed versions
df.insert(loc=1, column="processed_quotes", value=processed_data.split('nextquote')[:-1], allow_duplicates=True) 

FileNotFoundError: [Errno 2] No such file or directory: '../parsing/data/cleaned_tagged.txt'

In [7]:
df

quotes  \
0      Выкинь все, что есть в твоих мыслях: грусть, п...   
1      Порой молчание, красноречивее любых произнесен...   
2      А вы знаете, жизнь ведь замечательна и удивите...   
3                              - А че он такой красивый?   
4      Не тот велик, кто никогда не падал, а тот вели...   
...                                                  ...   
12522  Величайшая твердость и есть величайшее милосер...   
12523   Ничто великое в мире не совершается без страсти.   
12524                           Бог рад нечетному числу.   
12525             Иные утверждают, что душа есть воздух.   
12526  Писатель существует только тогда, когда тверды...   

                                        processed_quotes  
0      выкидывать твой мысль грусть пустота печаль по...  
1       пора молчание красноречиво любой произносить ...  
2       знать жизнь замечательный удивительный услови...  
3                                           че красивый   
4                большой падать большой падать вставать   
...                                                  ...  
12522              великий твердость великий милосердие   
12523             ничто великий мир совершаться страсть   
12524                            бог рад нечетный число   
12525                       иной утверждать душа воздух   
12526           писатель существовать твердый убеждение   

[12527 rows x 2 columns]

In [9]:
quote_tokens = [q.split() for q in df['processed_quotes'].values.tolist()]
quote_words = [q.split() for q in df['quotes'].values.tolist()]

#print(quote_tokens[0])
#print(quote_words[0])

In [18]:
import gensim
from gensim.models import Word2Vec
# define a model with parameters
# and train it on our data
model_w2v = Word2Vec(quote_tokens, # data for model to train on
                 vector_size=32,         # embedding vector size
                 min_count=5,     # consider words that occured at least 5 times
                 window=3,
                 hs = 1).wv     # define context as a 3-word window around the target word

In [11]:
wordic ='мама'
model_w2v.get_vector(wordic)
model_w2v.most_similar(wordic)

print(len(model_w2v.index_to_key))

2680


In [12]:
n_words = 1000
words = model_w2v.index_to_key
word_vectors = [model_w2v.get_vector(word) for word in words]

In [13]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

pca = PCA(n_components=32)
pca.fit(word_vectors)
word_vectors_pca = pca.transform(word_vectors)
ss = StandardScaler().fit(word_vectors_pca)
word_vectors_pca = ss.transform(word_vectors_pca)

In [105]:
import bokeh.models as bm, bokeh.plotting as pl
from bokeh.io import output_notebook
output_notebook()

def draw_vectors(x, y, radius=10, alpha=0.25, color='blue',
                 width=600, height=400, show=True, **kwargs):
    if isinstance(color, str): color = [color] * len(x)
    data_source = bm.ColumnDataSource({ 'x' : x, 'y' : y, 'color': color, **kwargs })

    fig = pl.figure(active_scroll='wheel_zoom', width=width, height=height)
    fig.scatter('x', 'y', size=radius, color='color', alpha=alpha, source=data_source)

    fig.add_tools(bm.HoverTool(tooltips=[(key, "@" + key) for key in kwargs.keys()]))
    if show: pl.show(fig)
    return fig


draw_vectors(word_vectors_pca[:, 0], word_vectors_pca[:, 1], token=words)

Loading BokehJS ...

Figure(id='1514', ...)

In [28]:
from sklearn.manifold import TSNE

tsne = TSNE(n_components=2, verbose=32)
#tsne.fit(word_vectors)
word_vectors_tsne = tsne.fit_transform(word_vectors)

ss = StandardScaler().fit(word_vectors_tsne)
word_vectors_tsne = ss.transform(word_vectors_tsne)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1000 samples in 0.001s...
[t-SNE] Computed neighbors for 1000 samples in 0.032s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1000
[t-SNE] Mean sigma: 0.054294
[t-SNE] Computed conditional probabilities in 0.050s
[t-SNE] Iteration 50: error = 60.6410446, gradient norm = 0.3141488 (50 iterations in 10.512s)
[t-SNE] Iteration 100: error = 56.7306557, gradient norm = 0.2477854 (50 iterations in 9.714s)
[t-SNE] Iteration 150: error = 56.0499115, gradient norm = 0.2580498 (50 iterations in 10.091s)
[t-SNE] Iteration 200: error = 55.3717346, gradient norm = 0.2453297 (50 iterations in 9.621s)
[t-SNE] Iteration 250: error = 54.8031044, gradient norm = 0.2608456 (50 iterations in 9.518s)
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.803104
[t-SNE] Iteration 300: error = 0.8770762, gradient norm = 0.0010110 (50 iterations in 9.120s)
[t-SNE] Iteration 350: error = 0.8026948, gradient norm = 0.000

In [11]:
output_notebook()
draw_vectors(word_vectors_tsne[:, 0], word_vectors_tsne[:, 1], token=words)

NameError: name 'output_notebook' is not defined

In [ ]:
import gensim.downloader as api
pre_model = api.load('word2vec-ruscorpora-300')

[===-----------------------------------------------] 7.4% 14.7/198.8MB downloaded

In [15]:
wordic =preprocess_text('хочу')
model_w2v.get_vector(wordic)
print(*model_w2v.most_similar(positive=[wordic]))
print("vs ruscorpora")
word ='хотеть_VERB'
pre_model.get_vector(word)
print(*pre_model.most_similar(positive=[word]))


('изменяться', 0.9871472716331482) ('ценить', 0.9749559760093689) ('милый', 0.9732074737548828) ('получаться', 0.972845196723938) ('сбываться', 0.9724627733230591) ('означать', 0.9719640612602234) ('кричать', 0.9718726873397827) ('злословие', 0.9704494476318359) ('красивый', 0.9704354405403137) ('посмотреть', 0.9702513813972473)
vs ruscorpora
('захотеть_VERB', 0.7732996940612793) ('желать_VERB', 0.7239466905593872) ('хотеться_VERB', 0.7220498323440552) ('захотеться_VERB', 0.62186598777771) ('полюбин_NOUN', 0.6022353172302246) ('нужно_ADV', 0.6014082431793213) ('валерьяна::александрыч_NOUN', 0.5812994241714478) ('фрейлен::минный_NOUN', 0.5723892450332642) ('юрьюшка_NOUN', 0.5544917583465576) ('вздумать_VERB', 0.5534098148345947)


Далее следуют эксперименты с Doc2vec

In [1]:
#preparing data for doc2vec
def tagged_document(list_of_list_of_words):
    for i, list_of_words in enumerate(list_of_list_of_words):
        yield gensim.models.doc2vec.TaggedDocument(list_of_words, [i])
quotes_for_training = list(tagged_document(quote_tokens))


NameError: name 'quote_tokens' is not defined

In [5]:
#buiding a model
model = gensim.models.doc2vec.Doc2Vec(vector_size=50, min_count=2, epochs=30)
model.build_vocab(quotes_for_training)
model.train(quotes_for_training, total_examples=model.corpus_count, epochs=model.epochs)

NameError: name 'gensim' is not defined

In [45]:
model.save('models/d2v_exp.model')

In [24]:
model = gensim.models.doc2vec.Doc2Vec.load('models/d2v.model')

In [110]:
request = request_processing()

sim = model.dv.most_similar(model.infer_vector(request), topn=Q_NUMBER)
avg, cluster_coefs = cluster_check(sim, model)
cluster_dict = dict(cluster_coefs)
print(avg)
for quote in sim:
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3), round(cluster_dict[quote[0]], 3))

print("--------------------------------------------vs old---------------------------------------------------")


sims = model_d2v.dv.most_similar(model_d2v.infer_vector(request), topn=Q_NUMBER)
avg, cluster_coefs = cluster_check(sims, model_d2v)
cluster_dict = dict(cluster_coefs)
print(avg)
for quote in sims:
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3), round(cluster_dict[quote[0]], 3))



мнения моих друзей поделись пополам, чью же сторону мне выбрать
0.7816300749778747
Не пытайся понять непонятное, друг, 0.797 0.631
Лучше человеку быть без брата, чем без друзей. 0.79 0.766
Души людей, как в зеркалах, отражаются друг в друге. 0.789 0.783
Омой, брат, руки от того друга, который водится с твоими врагами. 0.786 0.786
Чтобы быть ближе друг к другу,не обязательно лезть в душу-оценивая характер и взгляд партнера. 0.785 0.587
Чем быть с друзьями славными в разлуке. 0.78 0.79
Отдавая друг другу себя. 0.778 0.773
Настоящим другом считай того человека, который убирает камни и тернии с пути твоего. 0.776 0.617
Только рука друга может вырвать шипы из сердца. 0.772 0.718
Тот враг опаснее, который притворяется твоим другом. 0.763 0.72
--------------------------------------------vs old---------------------------------------------------
0.8153749287128449
По своим природным задаткам люди друг другу близки, а по своим привычкам друг от друга далеки. 0.861 0.623
Друга своего хваля, себя 

In [84]:
def cosine_similarity(u, v):
    """
    Cosine similarity reflects the degree of similarity between u and v
        
    Arguments:
        u -- a word vector of shape (n,)          
        v -- a word vector of shape (n,)

    Returns:
        cosine_similarity -- the cosine similarity between u and v defined by the formula above.
    """    
    # Special case. Consider the case u = [0, 0], v=[0, 0]
    if np.all(u == v):
        return 1    
    # Compute the dot product between u and v (≈1 line)
    dot = np.dot(u,v)
    # Compute the L2 norm of u (≈1 line)
    norm_u = np.sqrt(np.sum(u*u))    
    # Compute the L2 norm of v (≈1 line)
    norm_v = np.sqrt(np.sum(v*v))    
    # Avoid division by 0
    if np.isclose(norm_u * norm_v, 0, atol=1e-32):
        return 0    
    # Compute the cosine similarity defined by formula (1) (≈1 line)
    cosine_similarity = dot / (norm_u * norm_v)
    ### END CODE HERE ###    
    return cosine_similarity

In [86]:
a = model.infer_vector(preprocess_text("выбрать полезное или то что хочется?").split())
b = model.infer_vector(preprocess_text("То, что ты ищешь всю жизнь, может быть ближе, чем ты думаешь. Оглянись!").split())
cosine_similarity(a, b)

0.47603798

In [107]:
def cluster_check(sim, model):
    avg = sum([sim_coef for docid, sim_coef in sim])/len(sim)
    cluster_coef=[]
    for q in sim:
        q_sim = model.dv.most_similar(model.infer_vector(df['processed_quotes'][q[0]].split()), topn=len(df))
        q_dict = {}
        q_dict = dict(q_sim)
        q_sim_sim = [q_dict[docid] for docid, sim_coef in sim if docid != q[0]]
        cluster_coef.append((q[0],sum(q_sim_sim)/len(q_sim_sim)))
    return avg, cluster_coef

In [108]:
cluster_check(sim, model)

(0.7369030296802521,
 [(3103, 0.7399852209621005),
  (2801, 0.6307739946577284),
  (4563, 0.590758525662952),
  (10, 0.7638574441274008),
  (3418, 0.6000270446141561),
  (5750, 0.82101661629147),
  (9903, 0.6566664245393541),
  (8017, 0.5980288849936591),
  (773, 0.6559355921215482),
  (6865, 0.7431906792852614)])

In [43]:
#vectors of quotes for visualization
quote_vectors = [model.infer_vector(q) for q in quote_tokens]

In [44]:
#downsizing decompozition and later vectors ploting on the plane
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

pca = PCA(n_components=40)
pca.fit(quote_vectors)
word_vectors_pca = pca.transform(quote_vectors)
ss = StandardScaler().fit(word_vectors_pca)
word_vectors_pca = ss.transform(word_vectors_pca)

In [66]:
import bokeh.models as bm, bokeh.plotting as pl
from bokeh.io import output_notebook
output_notebook()

def draw_vectors(x, y, radius=10, alpha=0.25, color='blue',
                 width=600, height=400, show=True, **kwargs):
    if isinstance(color, str): color = [color] * len(x)
    data_source = bm.ColumnDataSource({ 'x' : x, 'y' : y, 'color': color, **kwargs })

    fig = pl.figure(active_scroll='wheel_zoom', width=width, height=height)
    fig.scatter('x', 'y', size=radius, color='color', alpha=alpha, source=data_source)

    fig.add_tools(bm.HoverTool(tooltips=[(key, "@" + key) for key in kwargs.keys()]))
    if show: pl.show(fig)
    return fig


draw_vectors(word_vectors_pca[:, 0], word_vectors_pca[:, 1], token=quote_tokens)

Loading BokehJS ...

Figure(id='1115', ...)

In [ ]:
from sklearn.manifold import TSNE

tsne = TSNE(n_components=2, verbose=32)
#tsne.fit(word_vectors)
word_vectors_tsne = tsne.fit_transform(word_vectors)

ss = StandardScaler().fit(word_vectors_tsne)
word_vectors_tsne = ss.transform(word_vectors_tsne)

In [66]:
ranks = []
second_ranks = []
for doc_id in range(len(quotes_for_training)):
    inferred_vector = model.infer_vector(quotes_for_training[doc_id].words)
    sims = model.dv.most_similar([inferred_vector], topn=len(model.dv))
    rank = [docid for docid, sim in sims].index(doc_id)
    ranks.append(rank)

    second_ranks.append(sims[1])

In [41]:
q_num = 1045
inferred_vector = model.infer_vector(quotes_for_training[q_num].words)
sims = model.dv.most_similar([inferred_vector], topn=len(model.dv))
rank = [docid for docid, sim in sims].index(q_num)
sims


[(8908, 0.8890571594238281),
 (12293, 0.7532801032066345),
 (5635, 0.7443583607673645),
 (7789, 0.7374767065048218),
 (8925, 0.7331910729408264),
 (7415, 0.7292873859405518),
 (3451, 0.7180445194244385),
 (9964, 0.7158632874488831),
 (7010, 0.7142969369888306),
 (4464, 0.7142553329467773),
 (6523, 0.7134678959846497),
 (5717, 0.7106955051422119),
 (10290, 0.7068539261817932),
 (6697, 0.7051745653152466),
 (10309, 0.7042885422706604),
 (11572, 0.7005789875984192),
 (12402, 0.699104368686676),
 (8943, 0.6980234384536743),
 (6277, 0.6967461705207825),
 (2741, 0.6912320256233215),
 (3027, 0.6866324543952942),
 (10926, 0.6858252286911011),
 (4168, 0.6835896372795105),
 (1692, 0.6821978092193604),
 (8997, 0.6811462044715881),
 (5389, 0.6765351295471191),
 (3130, 0.6740803122520447),
 (2964, 0.6728955507278442),
 (3357, 0.6680867671966553),
 (6328, 0.6660906672477722),
 (9788, 0.6651768684387207),
 (7164, 0.6651663184165955),
 (4713, 0.6634217500686646),
 (7521, 0.6627073884010315),
 (4493, 0

In [40]:
#inferred_vector = model.infer_vector(quotes_for_training[0].words)
sim = model.dv.most_similar(model.infer_vector(quotes_for_training[q_num].words), topn=10)
#print(quote_tokens[q_num])
print(" ".join(quote_words[q_num]))
print("\n -------------------------------------------------suggestions----------------------------------------------\n")
for quote in sim:
    #print(quote_tokens[quote[q_num]], round(quote[1], 3))
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3))

Человек всегда находит ложь, которая ему необходима, причем так же точно и быстро, как и необходимую ему правду, если вообще ощущает необходимость в правде.

 -------------------------------------------------suggestions----------------------------------------------

Человек всегда находит ложь, которая ему необходима, причем так же точно и быстро, как и необходимую ему правду, если вообще ощущает необходимость в правде. 0.927
Искажая правду-порождаем ложь. 0.795
Ищите же прежде Царства Божия и правды Его, и это все приложится вам. 0.79
Своя правда дороже чужой истины! 0.778
Честность есть простейшее выражение принципа правды. 0.775
Если тронуть страсти в человеке, То, конечно, правды не найдешь. 0.769
Своя правда дороже чужой истины! 0.767
Ложь, повторенная тысячу раз, становится правдой. 0.76
Подобно тому как комплимент бывает редко без лжи, так и грубость редко бывает без известной доли правды. 0.752
А в речи правды - тьма ошибок, и слог нестройностью увечен. 0.751


In [25]:
#request handling
request = preprocess_text(input()).split()
sim = model.dv.most_similar(model.infer_vector(request), topn=10)

print("\n -------------------------------------------------wise response----------------------------------------------\n")
for quote in sim:
    #print(quote_tokens[quote[q_num]], round(quote[1], 3))
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3))

почему так тяжело жить?

 -------------------------------------------------wise response----------------------------------------------

Мы не вправе жить, когда погибла честь. 0.777
Легендами становятся те кто, живут самим собой уважая себя! 0.768
Жестоким стало не общество,жестокими стали мы. 0.762
Человек не может жить без уверенности в том, что он кому-то нужен, что его любят. 0.754
Когда кто-то говорит, что научился жить без тебя. Ты уже в дураках, чтобы ты ни сказал. 0.731
Не учите меня жить, лучше помогите материально! 0.729
Есть люди столь скупые, как если бы они собирались жить вечно, и столь расточительные, как если бы собирались умереть завтра. 0.725
С дураками жить намного проще,им не надо навязывать себя. 0.718
Если рабы будут ждать свободы до тех пор, пока они не поумнеют, ждать придется долго... 0.718
Есть люди столь скупые, как если бы они собирались жить вечно, и столь расточительные, как если бы собирались умереть завтра. 0.716


Подготовка к мерджу, эссенсия функционала по функциям:


In [2]:
qoute_path = '../parsing/data/cleaned_tagged.txt'

df = pd.read_csv(qoute_path, sep='<\d*>', engine ='python', names=['quotes']) #reading quotes to the dataframe
with open(qoute_path, 'r', encoding='utf-8') as file:
    data = file.read().replace('\n', ' nextquote ')
    processed_data = preprocess_text(data)  #preprocessing qoutes
#dataframe with quotes and their processed versions
df.insert(loc=1, column="processed_quotes", value=processed_data.split('nextquote')[:-1], allow_duplicates=True) 

df.to_csv('processed_q.csv', columns=['quotes', 'processed_quotes'], index=False)

NameError: name 'preprocess_text' is not defined

Libriaris:

In [3]:
#preprocessing libriaris
import nltk
nltk.download("stopwords")
#stopwords modules
from nltk.corpus import stopwords
from pymystem3 import Mystem
from string import punctuation
#for work with data
import pandas as pd
import numpy as np
import io
#nlp libriaris
import gensim

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Files loading:

In [4]:
#files:
#Create lemmatizer and stopwords list
mystem = Mystem() 
russian_stopwords = stopwords.words("russian")
#reading csv
df = pd.read_csv('processed_q.csv', engine ='python')
#lists of quotes
quote_tokens = [q.split() for q in df['processed_quotes'].values.tolist()]
quote_words = [q.split() for q in df['quotes'].values.tolist()]

#model downloading
model_d2v = gensim.models.doc2vec.Doc2Vec.load('models/d2v.model')
#suggested quotes
Q_NUMBER = 10

Funcions:

In [5]:
#Preprocess function (stopwords, puncuation, etc)
def preprocess_text(text):
    tokens = mystem.lemmatize(text.lower())
    tokens = [token for token in tokens if token not in russian_stopwords\
              and token != " " \
              and token.strip() not in punctuation]   
    text = " ".join(tokens)    
    return text

#request handling
def request_processing():
    request = preprocess_text(input()).split()
    return request

main

In [50]:
sim = model_d2v.dv.most_similar(model_d2v.infer_vector(request_processing()), topn=Q_NUMBER)

for quote in sim:
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3))

амогус сус амогус сусси бака пипи ля пупу
Изменить себя и свой взгляд на мир - глупость и зависть мешает. 0.539
коль изменить ничто не в силах 0.537
Никто не может вызвать в вас чувство собственной неполноценности без вашего согласия. 0.532
Иногда,чтобы изменить судьбу-стоит изменить самого себя. 0.532
Когда тебе покажется что цель недостижима, не изменяй цель - изменяй план действий. 0.521
Молитва не может изменить волю Бога, но может изменить молящегося. 0.516
Одним из основных определений чести является то, что никто не должен своими поступками давать кому бы то ни было преимущества над собой. 0.483
должны Бога познавать через душу. 0.477
Никому не дано знать душу другого человека. 0.473
Чем больше окружающие знают, что из себя вы представляете и что от вас следует ожидать, тем сильнее это ограничивает вашу свободу. 0.472


сравнение со случайным цитатами:

In [22]:
import random
random_quotes = list(df['quotes'][np.random.choice(len(df), 10)])
for i in random_quotes:
    print(i)

У всякого человека в отдельности и у всех вместе есть, можно сказать, известная цель, стремясь к которой они одно избирают, другого избегают.
Радость более совершенна, чем знание, ибо не каждый в процессе познания радуется, но всякий, кто радуется, по необходимости при этом познает.
Зло с добром не вали без разбора на небо:
Если хочешь познать самого себя, то посмотри, как это делают другие; если же хочешь других понять, то посмотри в свое собственное сердце.
Любовь - это как слава при жизни. Мало родиться способным любить, необходимо еще благоволение судьбы, чтобы встретить ту единственную, тебе предназначенную Богом.
А ведь смерть добрая. Только жизнь причиняет страдания. Но мы любим жизнь и ненавидим смерть. Это очень странно.
Женщине необходим баланс: чтобы ее любили все, а она одного.
Основы каждого государства и фундамент любой страны покоятся на справедливости и правосудии.
Дружба не такой жалкий огонек, чтобы потухнуть в разлуке.
Потерянная душа никогда не обретет счастье даже 